In [4]:
%load_ext lab_black

In [5]:
# one hot encode runway
# ordinal encode airline
# TODO: Try with avg pb time, ratioH/M, ratio nominal
from traffic.core import Traffic

import pandas as pd
import numpy as np
import pickle

import os.path

from ipyleaflet import Polygon
from ipywidgets import Layout
from ipyleaflet import Map, Marker

import altair as alt

from cartes.osm import Overpass

from sklearn import svm

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import classification_report, confusion_matrix

from numpy import mean
from numpy import std
from sklearn.compose import ColumnTransformer
from sklearn.datasets import fetch_openml
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder, OrdinalEncoder
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split, GridSearchCV

In [6]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [8]:
dep_arr_df_2 = pd.read_pickle(
    "../data/processed/dep_arr_df12_onehotconfig_addedsifis.pkl"
)

In [14]:
dep_arr_df = pd.read_pickle(
    "../data/processed/dep_arr_df12_onehotconfig_addedsifis.pkl"
)

In [9]:
t_dep = Traffic.from_file("../data/intermediate/taxi_zurich_2019_takeoff.pkl")

In [15]:
def compute_avg_duration(
    dep_df,
    dt="30T",
    time_col="on_runway_time",
    on_col="total_holding_time_minutes",
    col_name="avg_delay",
):
    # Index is on_runway_time because it makes more sense to compute average
    # ground delays with flights having completed their taxi
    avg_delays = (
        dep_df.set_index(time_col)
        .sort_index()[on_col]
        .rolling(dt)  # closed="left" not needed as it is the target variable
        .agg("mean")
        .rename(col_name)
    )
    dep_df = pd.merge_asof(
        dep_df.sort_values(time_col),
        avg_delays,
        left_on=time_col,
        right_index=True,
    )
    return dep_df

In [20]:
full_taxiing_taxiholdavg_df = dep_arr_df_2.query(
    'mvt_type=="DEP" & parking_position==parking_position'
)
full_taxiing_taxiholdavg_df = compute_avg_duration(
    full_taxiing_taxiholdavg_df,
    on_col="taxi_holding_time_minutes",  # "taxi_holding_time_minutes",
    col_name="avg_taxi_delay",
)
datachart = full_taxiing_taxiholdavg_df[["first_movement_start", "avg_taxi_delay"]]
full_taxiing_taxiholdavg_chart = (
    alt.Chart(datachart)
    .transform_density("avg_taxi_delay", extent=(0, 14))
    .mark_line(color="green")
    .encode(x="value:Q", y="density:Q")
)

all_taxiholdavg_df = dep_arr_df.query('mvt_type=="DEP"')
all_taxiholdavg_df = compute_avg_duration(
    all_taxiholdavg_df,
    on_col="taxi_holding_time_minutes",  # "taxi_holding_time_minutes",
    col_name="avg_taxi_delay",
)
datachart = all_taxiholdavg_df[["first_movement_start", "avg_taxi_delay"]]
all_taxiholdavg_chart = (
    alt.Chart(datachart)
    .transform_density("avg_taxi_delay", extent=(0, 14))
    .mark_line(color="blue")
    .encode(x="value:Q", y="density:Q")
)

long_enough_taxiholdavg_df = dep_arr_df.query(
    'mvt_type=="DEP" & (parking_position==parking_position | taxi_dist>300)'
)
long_enough_taxiholdavg_df = compute_avg_duration(
    long_enough_taxiholdavg_df,
    on_col="taxi_holding_time_minutes",  # "taxi_holding_time_minutes",
    col_name="avg_taxi_delay",
)
datachart = long_enough_taxiholdavg_df[["first_movement_start", "avg_taxi_delay"]]
long_enough_taxiholdavg_chart = (
    alt.Chart(datachart)
    .transform_density("avg_taxi_delay", extent=(0, 14))
    .mark_line(color="orange")
    .encode(x="value:Q", y="density:Q")
)

In [21]:
long_enough_taxiholdavg_chart + full_taxiing_taxiholdavg_chart + all_taxiholdavg_chart

alt.LayerChart(...)

# Runway

In [1]:
" ".join(dep_arr_df_2.columns)

NameError: name 'dep_arr_df_2' is not defined

In [23]:
datachart = dep_arr_df_2.query(
    "mvt_type=='DEP' & (parking_position==parking_position | taxi_dist>300) & rwy__16==1"
)[["taxi_holding_time_minutes"]]
c1 = (
    alt.Chart(datachart)
    .transform_density(
        "taxi_holding_time_minutes", extent=[0, 25], as_=["Additional TXOT", "density"]
    )
    .mark_line(color="blue")
    .encode(x="Additional TXOT:Q", y="density:Q")
)
print(len(datachart))

datachart = dep_arr_df_2.query(
    "mvt_type=='DEP' & (parking_position==parking_position | taxi_dist>300) & rwy__32==1"
)[["taxi_holding_time_minutes"]]
c2 = (
    alt.Chart(datachart)
    .transform_density(
        "taxi_holding_time_minutes", extent=[0, 25], as_=["Additional TXOT", "density"]
    )
    .mark_line(color="red")
    .encode(x="Additional TXOT:Q", y="density:Q")
)
print(len(datachart))

datachart = dep_arr_df_2.query(
    "mvt_type=='DEP' & (parking_position==parking_position | taxi_dist>300) & rwy__28==1"
)[["taxi_holding_time_minutes"]]
c3 = (
    alt.Chart(datachart)
    .transform_density(
        "taxi_holding_time_minutes", extent=[0, 25], as_=["Additional TXOT", "density"]
    )
    .mark_line(color="green")
    .encode(x="Additional TXOT:Q", y="density:Q")
)
print(len(datachart))


(c1 + c2 + c3)

2154
3092
8528


alt.LayerChart(...)

In [45]:
(c1 + c2  + c3) # full trajs

alt.LayerChart(...)

In [43]:
(c1 + c2  + c3)

alt.LayerChart(...)

In [48]:
dep_arr_df_12 = pd.read_pickle(
    "../data/processed/dep_arr_df12_onehotconfig_addedsifis.pkl"
)

In [35]:
config_cols = ["rwy__EAST", "rwy__NORTH0", "rwy__SOUTH"]
datachart = dep_arr_df_2.query('mvt_type=="DEP" & parking_position==parking_position')[
    ["taxi_holding_time_minutes"] + config_cols
]

alt.Chart(datachart).transform_fold(
    config_cols, as_=["key_config", "value_config"]
).transform_filter("datum.value_config==1").transform_density(
    "taxi_holding_time_minutes", extent=[0, 16], groupby=["key_config"]
).mark_line().encode(
    alt.X("value:Q"), alt.Y("density:Q"), alt.Color("key_config:N")
)

alt.Chart(...)

In [49]:
datachart = dep_arr_df_12.query(
    'mvt_type=="DEP" & parking_position==parking_position & config==config & config!="NORTH1"'
)[["avg_delay_30min", "config"]]
alt.Chart(datachart).transform_density(
    "avg_delay_30min",
    extent=[0, 16],
    groupby=["config"],
    as_=["Additional TXOT averages", "density"],
).mark_line().encode(
    alt.X("Additional TXOT averages:Q"), alt.Y("density:Q"), alt.Color("config:N")
)

alt.Chart(...)

In [79]:
long_enough_taxiholdavg_df = dep_arr_df.query('mvt_type=="DEP" & (parking_position==parking_position | taxi_dist>500)')
long_enough_taxiholdavg_df = compute_avg_duration(
    long_enough_taxiholdavg_df,
    on_col="taxi_holding_time_minutes",  # "taxi_holding_time_minutes",
    col_name="avg_taxi_delay",
)
datachart = long_enough_taxiholdavg_df.query('mvt_type=="DEP" & config==config & config!="NORTH1"')[['avg_taxi_delay', 'config']]
long_enough_taxiholdavg_chart = alt.Chart(datachart).transform_density('avg_taxi_delay', extent=[0,16], groupby=['config'], as_ = ['Additional TXOT averages', 'density']).mark_line(strokeDash=[1,1]).encode(alt.X('Additional TXOT averages:Q'), alt.Y('density:Q'), alt.Color('config:N'))
long_enough_taxiholdavg_chart


alt.Chart(...)

In [78]:
all_taxiholdavg_df = dep_arr_df_2.query('mvt_type=="DEP" & (parking_position==parking_position)')
all_taxiholdavg_df = compute_avg_duration(
    all_taxiholdavg_df,
    on_col="taxi_holding_time_minutes",  # "taxi_holding_time_minutes",
    col_name="avg_taxi_delay",
)
datachart = all_taxiholdavg_df.query('mvt_type=="DEP" & config==config & config!="NORTH1"')[['avg_taxi_delay', 'config']]
all_f_chart = alt.Chart(datachart).transform_density('avg_taxi_delay', extent=[0,16], groupby=['config'], as_ = ['Additional TXOT averages', 'density']).mark_line().encode(alt.X('Additional TXOT averages:Q'), alt.Y('density:Q'), alt.Color('config:N'))
all_f_chart

alt.Chart(...)

In [80]:
long_enough_taxiholdavg_chart + all_f_chart

alt.LayerChart(...)

In [56]:
dep_arr_df_2.query('mvt_type=="DEP" & config==config').config.value_counts()

NORTH0    12945
EAST       2380
SOUTH      1577
NORTH1        3
Name: config, dtype: int64

In [60]:
rwy_count_df = dep_arr_df_2.query('mvt_type=="DEP"')[['first_movement_start', 'rwy__10', 'rwy__14', 'rwy__16', 'rwy__28', 'rwy__32', 'rwy__34'] ].sort_values('first_movement_start').set_index('first_movement_start').rolling("30T", closed='left').sum().add_suffix('_count')
dep_arr_df_3 = pd.merge_asof(dep_arr_df_2,rwy_count_df, left_on='first_movement_start', right_index=True)
dep_arr_df_3

flight_id            on_runway_time taxi_holding_time  \
0      GSW4942_15738 2019-10-01 04:00:28+00:00   0 days 00:01:23   
1        EDW200_5718 2019-10-01 04:10:37+00:00   0 days 00:01:18   
2       SWR177_15809 2019-10-01 04:05:11+00:00   0 days 00:00:00   
3       SWR139_15706 2019-10-01 04:07:25+00:00   0 days 00:00:00   
4       SWR296_13638 2019-10-01 04:09:53+00:00   0 days 00:00:00   
...              ...                       ...               ...   
36005   SWR176_15653 2019-11-30 22:02:47+00:00   0 days 00:02:16   
36006   SWR288_13280 2019-11-30 21:49:46+00:00   0 days 00:02:03   
36007   THY8HD_18663 2019-11-30 21:49:30+00:00   0 days 00:00:00   
36008    SWR92_15689 2019-11-30 22:04:18+00:00   0 days 00:03:29   
36009   SWR138_15564 2019-11-30 22:12:48+00:00   0 days 00:00:00   

      rwy_holding_time total_holding_time  taxi_holding_time_minutes  \
0                 None    0 days 00:01:23                   1.383333   
1                 None    0 days 00:04:56                   1.300000   
2                 None    0 days 00:00:00                   0.000000   
3                 None    0 days 00:00:00                   0.000000   
4                 None    0 days 00:00:00                   0.000000   
...                ...                ...                        ...   
36005             None    0 days 00:15:41                   2.266667   
36006             None    0 days 00:02:03                   2.050000   
36007             None    0 days 00:00:00                   0.000000   
36008             None    0 days 00:09:35                   3.483333   
36009             None    0 days 00:00:00                   0.000000   

                 first_movement callsign registration typecode  ... rwy__28  \
0     2019-10-01 03:59:06+00:00  GSW4942       HB-JOG     A319  ...       0   
1     2019-10-01 04:03:36+00:00   EDW200       HB-IHZ     A320  ...       0   
2     2019-10-01 04:05:48+00:00   SWR177       HB-JNI     B77W  ...       0   
3     2019-10-01 04:07:33+00:00   SWR139       HB-JNG     B77W  ...       0   
4     2019-10-01 04:10:25+00:00   SWR296       HB-JHM     A333  ...       0   
...                         ...      ...          ...      ...  ...     ...   
36005 2019-11-30 21:44:51+00:00   SWR176       HB-JNJ     B77W  ...       0   
36006 2019-11-30 21:46:26+00:00   SWR288       HB-JHI     A333  ...       0   
36007 2019-11-30 21:49:52+00:00   THY8HD       TC-JTN     A321  ...       1   
36008 2019-11-30 21:53:56+00:00    SWR92         None     None  ...       0   
36009 2019-11-30 22:11:16+00:00   SWR138       HB-JNH     B77W  ...       0   

      rwy__32 rwy__34 total_holding_time_minutes_cat rwy__10_count  \
0           0       1                            0.0           NaN   
1           1       0                            1.0           0.0   
2           0       1                            0.0           0.0   
3           0       1                            0.0           0.0   
4           0       1                            0.0           0.0   
...       ...     ...                            ...           ...   
36005       0       0                            2.0           0.0   
36006       0       1                            0.0           0.0   
36007       0       0                            0.0           0.0   
36008       1       0                            2.0           0.0   
36009       1       0                            0.0           0.0   

       rwy__14_count rwy__16_count rwy__28_count rwy__32_count rwy__34_count  
0                NaN           NaN           NaN           NaN           NaN  
1                0.0           0.0           0.0           0.0           1.0  
2                0.0           0.0           0.0           0.0           1.0  
3                0.0           0.0           0.0           0.0           1.0  
4                0.0           0.0           0.0           0.0           1.0  
...              ...           ...           ...           ...   

In [ ]:
rwy_count_cols =['rwy__14_count', 'rwy__16_count', 'rwy__28_count', 'rwy__32_count', 'rwy__34_count'] 

dep_arr_df_3[['taxi_holding_time_minutes'] + rwy_count_cols].transform_fold(rwy_count_cols)

In [81]:
my_fids = (
    dep_arr_df_2.query(
     "first_movement_start.dt.month==10 & rwy__28==1 & mvt_type=='DEP' & (parking_position!=parking_position & taxi_dist<600)"
    )
    .flight_id
)

Traffic.from_flights([t_dep[f].onground() for f in my_fids]).map_leaflet(zoom=13)

Map(center=[47.45668304537936, 8.56887538052461], controls=(ZoomControl(options=['position', 'zoom_in_text', '…

In [73]:
len(my_fids) # 688 for deps on 28 <300

688

In [72]:
dep_arr_df_2.query("mvt_type=='DEP' & (parking_position!=parking_position & taxi_dist<300)").shape

(2054, 112)

In [74]:
dep_arr_df_2.query("mvt_type=='DEP' & (parking_position==parking_position | taxi_dist>300)").shape

(14878, 112)

In [75]:
dep_arr_df_2.query("mvt_type=='DEP' & (parking_position==parking_position)").shape

(7424, 112)

In [76]:
2054 + 14878

16932